# Recommender Systems Tutorial
In this tutorial, we'll provide a simple walkthrough of how to use Snorkel to to improve recommendations.
We will use the [Goodreads](https://sites.google.com/eng.ucsd.edu/ucsdbookgraph/home) dataset, from
"Item Recommendation on Monotonic Behavior Chains", RecSys'18 (Mengting Wan, Julian McAuley), and "Fine-Grained Spoiler Detection from Large-Scale Review Corpora", ACL'19, Mengting Wan, Rishabh Misra, Ndapa Nakashole, Julian McAuley.

In this dataset, we have user ratings and reviews for Young Adult novels from the Goodreads website, along with metadata (like `title` and `authors`) for the novels. We consider the task of predicting whether a user will read and like any given book.

In [1]:
import os

if os.path.basename(os.getcwd()) == "snorkel-tutorials":
    os.chdir("recsys")

## Loading Data

We start by running the `download_and_process_data` function. The function mainly returns the `data_train`, `data_test`, `data_val`, `data_val` dataframes, which correspond to our training, test, development, and validation sets. Each of those dataframes has the following fields:
* `user_idx`: A unique identifier for a user.
* `book_idx`: A unique identifier for a book that is being rated by the user.
* `book_idxs`: The set of books that the user has interacted with (read or planned to read).
* `review_text`: Optional text review written by the user for the book.
* `rating`: Either `0` (which means the user did not read or did not like the book) or `1` (which means the user read and liked the book). The `rating` field is missing for `data_train`.
Our objective is to predict whether a given user (represented by the set of book_idxs the user has interacted with) will read and like any given book. That is, we want to train a model that takes a set of `book_idxs` and a `book_idx` as input and predicts the `rating`.

In addition, `download_and_process_data` also returns the `df_books` dataframe, which contains one row per book, along with metadata for that book (such as `title` and `first_author`).

In [2]:
from utils import download_and_process_data

(data_train, data_test, data_dev, data_val), df_books = download_and_process_data()

df_books.head()

/home/ubuntu/snorkel-tutorials/.tox/recsys/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:516: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
/home/ubuntu/snorkel-tutorials/.tox/recsys/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:517: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
/home/ubuntu/snorkel-tutorials/.tox/recsys/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:518: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int16, 1)])
/home/ubuntu/snorkel-t

/home/ubuntu/snorkel-tutorials/.tox/recsys/lib/python3.6/site-packages/tensorboard/compat/tensorflow_stub/dtypes.py:541: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
/home/ubuntu/snorkel-tutorials/.tox/recsys/lib/python3.6/site-packages/tensorboard/compat/tensorflow_stub/dtypes.py:542: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
/home/ubuntu/snorkel-tutorials/.tox/recsys/lib/python3.6/site-packages/tensorboard/compat/tensorflow_stub/dtypes.py:543: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int16, 1)])
/

/home/ubuntu/snorkel-tutorials/recsys/utils.py:165: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  df_interactions_nz["rating_4_5"] = df_interactions_nz.rating.map(ratings_map)


authors  average_rating   book_id country_code  \
3             [293603]            4.35  10099492           US   
4            [4018722]            3.71  22642971           US   
5            [6537142]            3.89  31556136           US   
12  [6455200, 5227552]            3.90  18522274           US   
13            [187837]            3.19  17262776           US   

                                          description  is_ebook language_code  \
3   It all comes down to this.\nVlad's running out...      True           eng   
4   The future world is at peace.\nElla Shepherd h...      True           eng   
5   A gorgeously written and deeply felt literary ...      True                 
12  Zoe Vanderveen is on the run with her captor t...      True         en-US   
13  The war is over, but for thirteen-year-old Rac...      True           eng   

    ratings_count                                      similar_books  \
3             152  [25861113, 7430195, 18765937, 6120544, 3247550...   
4            1525  [20499652, 17934493, 13518102, 16210411, 17149...   
5             109                                                 []   
12            191  [25063023, 18553080, 17567752, 18126509, 17997...   
13            248  [16153997, 10836616, 17262238, 16074827, 13628...   

    text_reviews_count                                              title  \
3                    9  Twelfth Grade Kills (The Chronicles of Vladimi...   
4                  428                                  The Body Electric   
5                   45                                         Like Water   
12                   6              Volition (The Perception Trilogy, #2)   
13                  68                                    Little Red Lies   

    first_author  book_idx  
3         293603         0  
4        4018722         1  
5        6537142         2  
12       6455200         3  
13        187837         4

We look at a sample of the labeled development set. As an example, we want our final recommendations model to be able to predict that a user with `book_idxs` (25743, 22318, 7662, 6857, 83, 14495, 30664, ...) would either not read or not like the book with `book_idx` 22764 (first row), while a user with `book_idxs` (3880, 18078, 9092, 29933, 1511, 8560, ...) would read and like the book with `book_idx` 3181 (second row).

In [3]:
data_dev.sample(frac=1, random_state=12).head()

user_idx                                          book_idxs  book_idx  \
473571     18277  (5751, 31459, 22276, 25682, 5398, 2426, 17297,...      9737   
334907     12949  (1021, 6175, 9423, 25377, 29392, 25310, 8772, ...     20732   
191566      7421  (31156, 23840, 13565, 20487, 11675, 15470, 203...     31299   
31976       1251  (22766, 1794, 28234, 8024, 6908, 3584, 6705, 3...      9452   
706600     27440  (29875, 3432, 23782, 30880, 22976, 6269, 449, ...     23305   

        rating                                        review_text  
473571       1                                                NaN  
334907       0                                                NaN  
191566       1  Wonderful novel!!! I completely enjoyed this a...  
31976        1                                                NaN  
706600       0                                                NaN

## Writing Labeling Functions

If a user has interacted with several books written by an author, there is a good chance that the user will read and like other books by the same author. We express this as a labeling function, using the `first_author` field in the `df_books` dataframe.

In [4]:
POSITIVE = 1
NEGATIVE = 0
ABSTAIN = -1

In [5]:
from snorkel.labeling.lf import labeling_function

book_to_first_author = dict(zip(df_books.book_idx, df_books.first_author))
first_author_to_books_df = df_books.groupby("first_author")[["book_idx"]].agg(set)
first_author_to_books = dict(
    zip(first_author_to_books_df.index, first_author_to_books_df.book_idx)
)


@labeling_function()
def common_first_author(x):
    author = book_to_first_author[x.book_idx]
    same_author_books = first_author_to_books[author]
    num_read = len(set(x.book_idxs).intersection(same_author_books))
    return POSITIVE if num_read > 15 else ABSTAIN

We can also leverage the long text reviews written by users to guess whether they liked or disliked a book. For example, the third data_dev entry above has a review with the text '4.5 STARS', which indicates that the user liked the book. We write a simple LF that looks for similar phrases to guess the user's rating of a book. We interpret >= 4 stars to indicate a positive rating, while < 4 stars is negative.

In [6]:
low_rating_strs = [
    "one star",
    "1 star",
    "two star",
    "2 star",
    "3 star",
    "three star",
    "3.5 star",
    "2.5 star",
    "1 out of 5",
    "2 out of 5",
    "3 out of 5",
]
high_rating_strs = ["5 stars", "five stars", "four stars", "4 stars", "4.5 stars"]


@labeling_function()
def stars_in_review(x):
    if not isinstance(x.review_text, str):
        return ABSTAIN
    for low_rating_str in low_rating_strs:
        if low_rating_str in x.review_text.lower():
            return NEGATIVE
    for high_rating_str in high_rating_strs:
        if high_rating_str in x.review_text.lower():
            return POSITIVE
    return ABSTAIN

We can also run [TextBlob](https://textblob.readthedocs.io/en/dev/index.html), a tool that provides a pretrained sentiment analyzer, on the reviews, and use its polarity and subjectivity scores to estimate the user's rating for the book.

In [7]:
from snorkel.preprocess import preprocessor
from textblob import TextBlob


@preprocessor()
def textblob_polarity(x):
    if x.review_text:
        x.blob = TextBlob(str(x.review_text))
    else:
        x.blob = None
    return x


textblob_polarity.memoize = True

# Label high polarity reviews as positive.
@labeling_function(pre=[textblob_polarity])
def polarity_positive(x):
    if x.blob:
        if x.blob.polarity > 0.3:
            return POSITIVE
    return ABSTAIN


# Label high subjectivity reviews as positive.
@labeling_function(pre=[textblob_polarity])
def subjectivity_positive(x):
    if x.blob:
        if x.blob.subjectivity > 0.75:
            return POSITIVE
    return ABSTAIN


# Label low polarity reviews as negative.
@labeling_function(pre=[textblob_polarity])
def polarity_negative(x):
    if x.blob:
        if x.blob.polarity < 0.0:
            return NEGATIVE
    return ABSTAIN

In [8]:
from snorkel.labeling import PandasLFApplier, LFAnalysis

lfs = [
    stars_in_review,
    common_first_author,
    polarity_positive,
    subjectivity_positive,
    polarity_negative,
]

applier = PandasLFApplier(lfs)
L_dev = applier.apply(data_dev)
LFAnalysis(L_dev, lfs).lf_summary(data_dev.rating)

  0%|          | 0/85988 [00:00<?, ?it/s]

  0%|          | 39/85988 [00:00<03:41, 388.45it/s]

  0%|          | 113/85988 [00:00<03:09, 452.56it/s]

  0%|          | 144/85988 [00:00<04:02, 353.39it/s]

  0%|          | 173/85988 [00:00<04:45, 300.45it/s]

...

100%|█████████▉| 85778/85988 [02:15<00:00, 641.93it/s]

100%|█████████▉| 85858/85988 [02:15<00:00, 680.24it/s]

100%|█████████▉| 85937/85988 [02:15<00:00, 707.50it/s]

100%|██████████| 85988/85988 [02:15<00:00, 633.56it/s]

j Polarity  Coverage  Overlaps  Conflicts  Correct  \
stars_in_review        0   [0, 1]  0.017991  0.004408   0.002000     1244   
common_first_author    1      [1]  0.048565  0.001058   0.000326     2803   
polarity_positive      2      [1]  0.045053  0.013362   0.001233     3080   
subjectivity_positive  3      [1]  0.018817  0.013828   0.003303     1173   
polarity_negative      4      [0]  0.017398  0.004280   0.003512      933   

                       Incorrect  Emp. Acc.  
stars_in_review              303   0.804137  
common_first_author         1373   0.671216  
polarity_positive            794   0.795044  
subjectivity_positive        445   0.724969  
polarity_negative            563   0.623663

### Applying labeling functions to the training set

We apply the labeling functions to the training set, and then filter out examples unlabeled by any LF, and combine the rest with the dev set to form our final training set.

In [9]:
from snorkel.labeling.model.label_model import LabelModel

# Train LabelModel.
L_train = applier.apply(data_train)
label_model = LabelModel(cardinality=2, verbose=True)
label_model.fit(L_train, n_epochs=5000, seed=123, log_freq=20, lr=0.01)
Y_train_preds = label_model.predict(L_train)

  0%|          | 0/598271 [00:00<?, ?it/s]

  0%|          | 5/598271 [00:00<3:27:44, 48.00it/s]

  0%|          | 79/598271 [00:00<2:29:27, 66.71it/s]

  0%|          | 153/598271 [00:00<1:48:39, 91.74it/s]

  0%|          | 223/598271 [00:00<1:20:20, 124.07it/s]

...

100%|█████████▉| 598037/598271 [15:46<00:00, 593.19it/s]

100%|█████████▉| 598098/598271 [15:46<00:00, 443.51it/s]

100%|█████████▉| 598169/598271 [15:46<00:00, 499.41it/s]

100%|█████████▉| 598226/598271 [15:46<00:00, 516.13it/s]

100%|██████████| 598271/598271 [15:47<00:00, 631.71it/s]

In [10]:
import pandas as pd
from snorkel.labeling import filter_unlabeled_dataframe

data_train_filtered, Y_train_preds_filtered = filter_unlabeled_dataframe(
    data_train, Y_train_preds, L_train
)
data_train_filtered["rating"] = Y_train_preds_filtered
combined_data_train = pd.concat([data_train_filtered, data_dev], axis=0)

/home/ubuntu/snorkel-tutorials/.tox/recsys/lib/python3.6/site-packages/ipykernel_launcher.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  import sys
/home/ubuntu/snorkel-tutorials/.tox/recsys/lib/python3.6/site-packages/ipykernel_launcher.py:8: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  


### Rating Prediction Model
We write a Keras model for predicting ratings given a user's book list and a book (which is being rated). The model represents the list of books the user interacted with, `books_idxs`, by learning an embedding for each idx, and averaging the embeddings in `book_idxs`. It learns another embedding for the `book_idx`, the book to be rated. Then it concatenates the two embeddings and uses an [MLP](https://en.wikipedia.org/wiki/Multilayer_perceptron) to compute the probability of the `rating` being 1.

In [11]:
import numpy as np
import tensorflow as tf
from utils import precision, recall, f1

n_books = len(df_books)


# Keras model to predict rating given book_idxs and book_idx.
def get_model(embed_dim=64, hidden_layer_sizes=[32]):
    # Compute embedding for book_idxs.
    len_book_idxs = tf.keras.layers.Input([])
    book_idxs = tf.keras.layers.Input([None])
    book_idxs_emb = tf.keras.layers.Embedding(n_books, embed_dim)(book_idxs)
    book_idxs_emb = tf.math.divide(
        tf.keras.backend.sum(book_idxs_emb, axis=1), tf.expand_dims(len_book_idxs, 1)
    )
    # Compute embedding for book_idx.
    book_idx = tf.keras.layers.Input([])
    book_idx_emb = tf.keras.layers.Embedding(n_books, embed_dim)(book_idx)
    input_layer = tf.keras.layers.concatenate([book_idxs_emb, book_idx_emb], 1)
    # Build Multi Layer Perceptron on input layer.
    cur_layer = input_layer
    for size in hidden_layer_sizes:
        tf.keras.layers.Dense(size, activation=tf.nn.relu)(cur_layer)
    output_layer = tf.keras.layers.Dense(1, activation=tf.nn.sigmoid)(cur_layer)
    # Create and compile keras model.
    model = tf.keras.Model(
        inputs=[len_book_idxs, book_idxs, book_idx], outputs=[output_layer]
    )
    model.compile(
        "Adagrad", "binary_crossentropy", metrics=["accuracy", f1, precision, recall]
    )
    return model


# Generator to turn dataframe into examples.
def get_examples_generator(df):
    def generator():
        for book_idxs, book_idx, rating in zip(df.book_idxs, df.book_idx, df.rating):
            if len(book_idxs) <= 2:
                continue
            # Remove book_idx from book_idxs so the model can't just look it up.
            book_idxs = tuple(filter(lambda x: x != book_idx, book_idxs))
            yield {
                "len_book_idxs": len(book_idxs),
                "book_idxs": book_idxs,
                "book_idx": book_idx,
                "label": rating,
            }
            if rating == 1:
                # Generate random negative example.
                yield {
                    "len_book_idxs": len(book_idxs),
                    "book_idxs": book_idxs,
                    "book_idx": np.random.randint(0, n_books),
                    "label": 0,
                }

    return generator


def get_data_tensors(df):
    # Use generator to get examples each epoch, along with shuffling and batching.
    padded_shapes = {
        "len_book_idxs": [],
        "book_idxs": [None],
        "book_idx": [],
        "label": [],
    }
    dataset = (
        tf.data.Dataset.from_generator(
            get_examples_generator(df), {k: tf.int64 for k in padded_shapes}
        )
        .shuffle(123)
        .repeat(None)
        .padded_batch(batch_size=256, padded_shapes=padded_shapes)
    )
    tensor_dict = tf.compat.v1.data.make_one_shot_iterator(dataset).get_next()
    return (
        tensor_dict["len_book_idxs"],
        tensor_dict["book_idxs"],
        tensor_dict["book_idx"],
        tensor_dict["label"],
    )

We now train the model on our combined training data (data labeled by LFs plus dev data).


In [12]:
model = get_model()

train_data_tensors = get_data_tensors(combined_data_train)
val_data_tensors = get_data_tensors(data_val)
model.fit(
    train_data_tensors[:-1],
    train_data_tensors[-1],
    steps_per_epoch=300,
    validation_data=(val_data_tensors[:-1], val_data_tensors[-1]),
    validation_steps=40,
    epochs=50,
    verbose=1,
)

W0810 02:36:11.213353 140509380491072 deprecation.py:506] From /home/ubuntu/snorkel-tutorials/.tox/recsys/lib/python3.6/site-packages/tensorflow/python/keras/initializers.py:119: calling RandomUniform.__init__ (from tensorflow.python.ops.init_ops) with dtype is deprecated and will be removed in a future version.
Instructions for updating:
Call initializer instance with the dtype argument instead of passing it to the constructor


W0810 02:36:11.293188 140509380491072 deprecation.py:506] From /home/ubuntu/snorkel-tutorials/.tox/recsys/lib/python3.6/site-packages/tensorflow/python/ops/init_ops.py:1251: calling VarianceScaling.__init__ (from tensorflow.python.ops.init_ops) with dtype is deprecated and will be removed in a future version.
Instructions for updating:
Call initializer instance with the dtype argument instead of passing it to the constructor


W0810 02:36:11.406020 140509380491072 deprecation.py:323] From /home/ubuntu/snorkel-tutorials/.tox/recsys/lib/python3.6/site-packages/tensorflow/python/ops/nn_impl.py:180: add_dispatch_support.<locals>.wrapper (from tensorflow.python.ops.array_ops) is deprecated and will be removed in a future version.
Instructions for updating:
Use tf.where in 2.0, which has the same broadcast rule as np.where


W0810 02:36:11.428034 140509380491072 deprecation.py:323] From /home/ubuntu/snorkel-tutorials/.tox/recsys/lib/python3.6/site-packages/tensorflow/python/data/ops/dataset_ops.py:494: py_func (from tensorflow.python.ops.script_ops) is deprecated and will be removed in a future version.
Instructions for updating:
tf.py_func is deprecated in TF V2. Instead, there are two
    options available in V2.
    - tf.py_function takes a python function which manipulates tf eager
    tensors instead of numpy arrays. It's easy to convert a tf eager tensor to
    an ndarray (just call tensor.numpy()) but having access to eager tensors
    means `tf.py_function`s can use accelerators such as GPUs as well as
    being differentiable using a gradient tape.
    - tf.numpy_function maintains the semantics of the deprecated tf.py_func
    (it is not differentiable, and manipulates numpy arrays). It drops the
    stateful argument making all functions stateful.
    


W0810 02:36:11.612854 140509380491072 deprecation.py:506] From /home/ubuntu/snorkel-tutorials/.tox/recsys/lib/python3.6/site-packages/tensorflow/python/keras/optimizer_v2/adagrad.py:105: calling Constant.__init__ (from tensorflow.python.ops.init_ops) with dtype is deprecated and will be removed in a future version.
Instructions for updating:
Call initializer instance with the dtype argument instead of passing it to the constructor


...

293/300 [============================>.] - ETA: 0s - loss: 0.5839 - acc: 0.7117 - f1: 0.5010 - precision: 0.7834 - recall: 0.3745

295/300 [============================>.] - ETA: 0s - loss: 0.5839 - acc: 0.7114 - f1: 0.5008 - precision: 0.7839 - recall: 0.3741

297/300 [============================>.] - ETA: 0s - loss: 0.5835 - acc: 0.7117 - f1: 0.5008 - precision: 0.7839 - recall: 0.3741

299/300 [============================>.] - ETA: 0s - loss: 0.5827 - acc: 0.7126 - f1: 0.5008 - precision: 0.7847 - recall: 0.3740

300/300 [==============================] - 12s 41ms/step - loss: 0.5822 - acc: 0.7131 - f1: 0.5010 - precision: 0.7855 - recall: 0.3740 - val_loss: 0.6298 - val_acc: 0.6733 - val_f1: 0.4440 - val_precision: 0.6439 - val_recall: 0.3449


Finally, we evaluate the model's predicted ratings on our test data.


In [13]:
test_data_tensors = get_data_tensors(data_test)
model.evaluate(test_data_tensors[:-1], test_data_tensors[-1], steps=30)

 1/30 [>.............................] - ETA: 3s - loss: 0.6417 - acc: 0.6719 - f1: 0.4247 - precision: 0.5741 - recall: 0.3370

 3/30 [==>...........................] - ETA: 1s - loss: 0.6247 - acc: 0.6836 - f1: 0.4164 - precision: 0.6345 - recall: 0.3115

 5/30 [====>.........................] - ETA: 1s - loss: 0.6276 - acc: 0.6734 - f1: 0.4168 - precision: 0.6320 - recall: 0.3120

 7/30 [======>.......................] - ETA: 0s - loss: 0.6299 - acc: 0.6780 - f1: 0.4489 - precision: 0.6527 - recall: 0.3441

 9/30 [========>.....................] - ETA: 0s - loss: 0.6296 - acc: 0.6732 - f1: 0.4276 - precision: 0.6433 - recall: 0.3242

...

25/30 [========================>.....] - ETA: 0s - loss: 0.6337 - acc: 0.6709 - f1: 0.4612 - precision: 0.6690 - recall: 0.3568

27/30 [==========================>...] - ETA: 0s - loss: 0.6333 - acc: 0.6691 - f1: 0.4590 - precision: 0.6745 - recall: 0.3529

29/30 [============================>.] - ETA: 0s - loss: 0.6316 - acc: 0.6721 - f1: 0.4615 - precision: 0.6731 - recall: 0.3562

30/30 [==============================] - 1s 31ms/step - loss: 0.6316 - acc: 0.6720 - f1: 0.4625 - precision: 0.6734 - recall: 0.3571


[0.6315575500329336, 0.67200524, 0.46245655, 0.6734241, 0.3570875]